In [ ]:
!pip install Arabic-Stopwords

In [ ]:
pip install transformers

In [ ]:
pip install Tashaphyne

In [ ]:
pip install PyArabic

In [ ]:
# Add environment Packages paths to conda
import os, sys, warnings
import pandas as pd
import numpy as np
warnings.simplefilter("ignore")

# Text preprocessing packages
import nltk # Text libarary
# nltk.download('stopwords')
import string # Removing special characters {#, @, ...}
import re # Regex Package
import regex
#import emoji
# Corpora is a group presenting multiple collections of text documents. A single collection is called corpus.
from nltk.corpus import stopwords # Stopwords
import arabicstopwords.arabicstopwords as stp #more range of arabic stop words
from nltk.stem.isri import ISRIStemmer
import pyarabic.araby as araby
from tashaphyne.stemming import ArabicLightStemmer

from nltk.stem import SnowballStemmer, WordNetLemmatizer # Stemmer & Lemmatizer
#from gensim.utils import simple_preprocess  # Text ==> List of Tokens

# Text Embedding
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer

# Modelling
from sklearn.model_selection import train_test_split,KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score,confusion_matrix, classification_report
from sklearn.pipeline import Pipeline
from sklearn.metrics import f1_score
from sklearn.svm import SVC
# Saving Model
import pickle

# Visualization Packages
import seaborn as sns
import matplotlib.pyplot as plt
sns.set(font_scale=1.3)
%matplotlib inline

In [ ]:
#from google.colab import drive
#drive.mount('/content/drive')

In [ ]:
#df = pd.read_csv('/content/drive/MyDrive/CateringTWEPYEX4SentiV8.csv')

#df.head()

In [ ]:
df = pd.read_csv('../input/cateringhajj/CateringTWEPYEX4SentiV8.csv')

df.head()

In [ ]:
df.shape

In [ ]:
df.info()

In [ ]:
df.Sentiment.value_counts()

In [ ]:
df.isnull().sum()

In [ ]:
df[df['Tweet'].isnull() == True]

In [ ]:
df.duplicated().sum()

In [ ]:
df[df['Tweet'].duplicated() == True]

In [ ]:
df[df['Tweet'] == df.iloc[76]['Tweet']]

In [ ]:
import nltk
nltk.download('stopwords')

In [ ]:
#are there any stop words in the data?
arabic_stopwords = stopwords.words("arabic")
len(arabic_stopwords)

In [ ]:
def remove_stop_words(Tweet):
    Tweet=[i for i in str(Tweet).split() if i not in arabic_stopwords]
    return " ".join(Tweet)

def ISRI_Stemmer(Tweet):
    #making an object
    stemmer = ISRIStemmer()
    
    #stemming each word
    Tweet = stemmer.stem(Tweet)
    Tweet = stemmer.pre32(Tweet)
    Tweet = stemmer.suf32(Tweet)
    
    return Tweet

def Snowball_stemmer(Tweet):
    Tweet = Tweet.split()
    #making an object
    stemmer = SnowballStemmer("arabic")
    
    #stemming each word
    Tweet=[stemmer.stem(y) for y in Tweet]
    
    return " " .join(Tweet)

def Arabic_Light_Stemmer(Tweet):
    #making an object
    Arabic_Stemmer = ArabicLightStemmer()
    
    #stemming each word
    Tweet=[Arabic_Stemmer.light_stem(y) for y in Tweet.split()]
    
    return " " .join(Tweet)

def normalizeArabic(Tweet):
    Tweet = Tweet.strip()
    Tweet = re.sub("ى", "ي", Tweet)
    Tweet = re.sub("ؤ", "ء", Tweet)
    Tweet = re.sub("ئ", "ء", Tweet)
    Tweet = re.sub("ة", "ه", Tweet)
    
    #remove repetetions
    Tweet = re.sub("[إأٱآا]", "ا", Tweet)
    Tweet = Tweet.replace('وو', 'و')
    Tweet = Tweet.replace('يي', 'ي')
    Tweet = Tweet.replace('ييي', 'ي')
    Tweet = Tweet.replace('اا', 'ا')

    ## remove extra whitespace
    Tweet = re.sub('\s+', ' ', Tweet)
    
    # Remove longation
    Tweet = re.sub(r'(.)\1+', r"\1\1", Tweet) 
    
    #Strip vowels from a text, include Shadda.
    Tweet = araby.strip_tashkeel(Tweet)
    
    #Strip diacritics from a text, include harakats and small lettres The striped marks are
    Tweet = araby.strip_diacritics(Tweet)
    Tweet=''.join([i for i in Tweet if not i.isdigit()])
    return Tweet

def Removing_non_arabic(Tweet):
    Tweet = re.sub('[A-Za-z]+',' ',Tweet)
    return Tweet

def Removing_numbers(Tweet):
    Tweet=''.join([i for i in Tweet if not i.isdigit()])
    return Tweet

def Removing_punctuations(Tweet):
    ## Remove punctuations
    Tweet = re.sub('[%s]' % re.escape("""!"#$%&'()*+,،-./:;<=>؟?@[\]^_`{|}~"""), ' ', Tweet)
    Tweet = Tweet.replace('؛',"", )
    
    ## remove extra whitespace
    Tweet = re.sub('\s+', ' ', Tweet)
    Tweet =  " ".join(Tweet.split())
    return Tweet.strip()

def Removing_urls(Tweet):
    url_pattern = re.compile(r'https?://\S+|www\.\S+')
    return url_pattern.sub(r'', Tweet)




def remove_extra_Space(Tweet):
    ## remove extra whitespace
    Tweet = re.sub('\s+', ' ', Tweet)
    return  " ".join(Tweet.split())

            
#def space_between_emojis(s): 
 #   return ''.join((' '+c+' ') if c in emoji.UNICODE_EMOJI['en'] else c for c in s)

def remove_hashtages_and_mentions(Tweet):
    Tweet = re.sub("@[A-Za-z0-9_]+","", Tweet)
    Tweet = re.sub("#[A-Za-z0-9_]+","", Tweet)
    return Tweet

In [ ]:
df.Tweet=df.Tweet.apply(lambda Tweet : remove_stop_words(Tweet))

In [ ]:
df.Tweet=df.Tweet.apply(lambda Tweet : Removing_non_arabic(Tweet))

In [ ]:
df.iloc[4621].Tweet

In [ ]:
df.Tweet=df.Tweet.apply(lambda Tweet : normalizeArabic(Tweet))

In [ ]:
df.iloc[1].Tweet

In [ ]:
df.Tweet=df.Tweet.apply(lambda Tweet : remove_hashtages_and_mentions(Tweet))

In [ ]:
df.iloc[0].Tweet

In [ ]:
df.Tweet=df.Tweet.apply(lambda Tweet : Removing_urls(Tweet))

In [ ]:
df.Tweet=df.Tweet.apply(lambda Tweet : Removing_punctuations(Tweet))

In [ ]:
df.iloc[0].Tweet

In [ ]:
df

In [ ]:
#df.Tweet=df.Tweet.apply(lambda Tweet : Arabic_Light_Stemmer(Tweet))

In [ ]:
df.duplicated().sum()

In [ ]:
df

In [ ]:
df.iloc[295].Tweet

In [ ]:
df.iloc[0].Tweet

#  تحميل الداتاسيت + المكاتب + الكليننق 
# ممتازة

In [ ]:
# Encode Categorical Variable
X = df['Tweet']
y = pd.get_dummies(df['Sentiment']).values
num_classes = df['Sentiment'].nunique()

In [ ]:
seed = 101 # fix random seed for reproducibility
np.random.seed(seed)

In [ ]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    test_size=0.1,
                                                    stratify=y,
                                                    random_state=seed)
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

In [ ]:
from keras.preprocessing.text import Tokenizer
max_features = 20000
tokenizer = Tokenizer(num_words=max_features)
tokenizer.fit_on_texts(list(X_train))
X_train = tokenizer.texts_to_sequences(X_train)
X_test = tokenizer.texts_to_sequences(X_test)

In [ ]:
totalNumWords = [len(one_comment) for one_comment in X_train]
plt.hist(totalNumWords,bins = 30)
plt.show()

In [ ]:
from tensorflow.keras.utils import pad_sequences
max_words = 30
X_train = pad_sequences(X_train, maxlen=max_words)
X_test = pad_sequences(X_test, maxlen=max_words)
print(X_train.shape,X_test.shape)

In [ ]:
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Input, Dense, Embedding, Conv1D, MaxPool1D, Dropout, SimpleRNN, LSTM, MaxPooling1D, BatchNormalization, Bidirectional, GlobalMaxPool1D
from tensorflow.keras.layers import Flatten
from tensorflow.keras.preprocessing import sequence

In [ ]:
#إضااافة 

from keras.metrics import Precision, Recall

In [ ]:
#إضااافة 

import keras.backend as K

def f1_score(precision, recall):
    ''' Function to calculate f1 score '''
    
    f1_val = 2*(precision*recall)/(precision+recall+K.epsilon())
    return f1_val

In [ ]:
from keras.layers import Embedding, Conv1D, MaxPooling1D, Bidirectional, LSTM, Dense, Dropout

In [ ]:
#======Optimization Function=======

from keras.optimizers import SGD
from tensorflow import keras

ADAM = keras.optimizers.Adam(learning_rate=0.001)

In [ ]:
#========Callback Function/Early Stopping======
# TensorFlow and tf.keras
import tensorflow as tf
from tensorflow import keras

callback = tf.keras.callbacks.EarlyStopping(monitor='val_accuracy',patience=4, restore_best_weights=True, verbose=1, mode='auto')

In [ ]:
  model = Sequential()
  model.add(Embedding(31157, 300, input_length=X_train.shape[1]))

  model.add(Conv1D(filters=128, kernel_size=4, padding='same', activation='relu'))
  model.add(MaxPool1D(pool_size=2))
  model.add(BatchNormalization())
    
  model.add(Conv1D(filters=128, kernel_size=4, padding='same',activation='relu'))
  model.add(MaxPool1D(pool_size=2))
  model.add(BatchNormalization())
    
 # model.add(Conv1D(filters=128, kernel_size=4, padding='same',activation='relu'))
  #model.add(MaxPool1D(pool_size=2))
  #model.add(BatchNormalization())
    
#  model.add(Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
#  model.add(MaxPool1D(pool_size=2)) 
#  model.add(BatchNormalization())
#  model.add(Dropout(0.2))
  
#  model.add(Conv1D(filters=32, kernel_size=3, padding='same', activation='relu')) 
 # model.add(MaxPool1D(pool_size=2))  
 # model.add(BatchNormalization())
 # model.add(Dropout(0.1))
 
 # model.add(Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
 # model.add(MaxPool1D(pool_size=2))
 # model.add(BatchNormalization())
#  model.add(Dropout(0.1))

  #model.add(Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
    
  model.add(Bidirectional(LSTM(100, dropout=0.5,activation='tanh', recurrent_dropout=0.1)))

  model.add(Dropout(0.5))  

  model.add(Flatten())

  model.add(Dense(3, activation='softmax'))
  model.compile(loss='categorical_crossentropy', optimizer=ADAM, metrics=['accuracy',  Precision(), Recall(), f1_score])
  print(model.summary())

In [ ]:
model_history = model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=30, batch_size=6, verbose=2, callbacks=[callback])

In [ ]:
def model_evaluate(): 
    # predict class with test set
    y_pred_test =  np.argmax(model.predict(X_test), axis=1)
    print('Accuracy:\t{:0.1f}%'.format(accuracy_score(np.argmax(y_test,axis=1),y_pred_test)*100))
    
    #classification report
    print('\n')
    print(classification_report(np.argmax(y_test,axis=1), y_pred_test))

    #confusion matrix
    confmat = confusion_matrix(np.argmax(y_test,axis=1), y_pred_test)
    
    sns.heatmap(confmat, annot=True, fmt='d', 
                xticklabels=['Negative', 'Positive', 'Natural'],yticklabels=['Negative', 'Positive', 'Natural'] )

    plt.ylabel('True label')
    plt.xlabel('Predicted label')
    plt.show()
#................................. Blue Box......

    fig, ax = plt.subplots(figsize=(4, 4))
    ax.matshow(confmat, cmap=plt.cm.Blues, alpha=0.3)
    for i in range(confmat.shape[0]):
        for j in range(confmat.shape[1]):
            ax.text(x=j, y=i, s=confmat[i, j], va='center', ha='center')

            
    plt.xlabel('Predicted label')
    plt.ylabel('True label')
    plt.tight_layout()
    
 #.................................

In [ ]:
# evaluate model with test set
model_evaluate()

In [ ]:
def plot_training_hist(model_history):
    '''Function to plot history for accuracy and loss'''
    
    fig, ax = plt.subplots(1, 2, figsize=(10,4))
    # first plot
    ax[0].plot(model_history.history['accuracy'])
    ax[0].plot(model_history.history['val_accuracy'])
    ax[0].set_title('Model Accuracy')
    ax[0].set_xlabel('Epoch')
    ax[0].set_ylabel('Accuracy')
    ax[0].legend(['train', 'validation'], loc='best')
    # second plot
    ax[1].plot(model_history.history['loss'])
    ax[1].plot(model_history.history['val_loss'])
    ax[1].set_title('Model Loss')
    ax[1].set_xlabel('Epoch')
    ax[1].set_ylabel('Loss')
    ax[1].legend(['train', 'validation'], loc='best')
    
plot_training_hist(model_history)

In [ ]:
#Done 

from keras.utils.vis_utils import plot_model
plot_model(model, show_shapes=True)

In [ ]:
#Done 
import pickle
with open('tokenizer.pickle', 'wb') as f:
    pickle.dump(tokenizer, f)
    
#with open('labelEncoder.pickle', 'wb') as f:
 #   pickle.dump(le, f)
    
    
model.save('My model-Hajj.h5')